<a href="https://colab.research.google.com/github/Mmian0125/ai/blob/main/tweet_disaster_prediction.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
from google.colab import drive
drive.mount('/content/drive')


Mounted at /content/drive


In [2]:
import pandas as pd
from transformers import AutoTokenizer,BertForSequenceClassification
import torch
import os
import torch.nn as nn
from tqdm import tqdm
from torch.utils.data import Dataset, DataLoader

In [3]:
model_root="/content/drive/MyDrive/model/bert-base-uncased"
data_root="/content/drive/MyDrive/tweet_disaster_dataset"
train_path=os.path.join(data_root,"train.csv")
test_path=os.path.join(data_root,"test.csv")
submission_path=os.path.join(data_root,"sample_submission.csv")

In [ ]:
#train_data=pd.read_csv(train_path)
#test_data=pd.read_csv(test_path)
#print(train_data)

In [4]:
class MyDataset(Dataset):
    def __init__(self, data_root, model_root,is_train=True):
        super().__init__()
        self.is_train=is_train
        data_path=os.path.join(data_root,"train.csv") if is_train==True else os.path.join(data_root,"test.csv")
        self.df_data=pd.read_csv(data_path)
        self.tokenizer=AutoTokenizer.from_pretrained(model_root,local_files_only=True)

    def __len__(self):
        return len(self.df_data)

    def __getitem__(self,index):
        text=self.df_data['text'][index]
        if self.is_train == True:
            label=self.df_data['target'][index]
        token=self.tokenizer(text=text, padding='max_length', max_length=128, truncation=True, return_tensors='pt')
        input_ids, attention_mask, token_type_ids=token['input_ids'].squeeze(0), token['attention_mask'].squeeze(0), token['token_type_ids'].squeeze(0)

        return (input_ids,attention_mask,token_type_ids, label) if self.is_train==True else (input_ids,attention_mask,token_type_ids)

In [5]:
train_dataset=MyDataset(data_root,model_root,True)
test_dataset=MyDataset(data_root,model_root,False)

In [6]:
class Params:
    batch_size=16
    shuffle=True
    num_workers=0
    lr=2e-5
    weight_decay=0.01
    epochs=25

In [7]:
train_iter=DataLoader(dataset=train_dataset,batch_size=Params.batch_size, shuffle=Params.shuffle, num_workers=Params.num_workers)
test_iter=DataLoader(dataset=test_dataset,batch_size=Params.batch_size, shuffle=Params.shuffle, num_workers=Params.num_workers)

In [8]:
model=BertForSequenceClassification.from_pretrained(model_root)
loss=nn.CrossEntropyLoss()
optimizer=torch.optim.AdamW(model.parameters(),lr=Params.lr,weight_decay=Params.weight_decay )

Some weights of BertForSequenceClassification were not initialized from the model checkpoint at /content/drive/MyDrive/model/bert-base-uncased and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [9]:
device=torch.device('cuda' if torch.cuda.is_available() else 'cpu')

In [10]:
model=model.to(device=device)
if torch.cuda.device_count()>1:
    model=nn.DataParallel(model)
loss=loss.to(device=device)

In [ ]:
for epoch in range(Params.epochs):
    process=tqdm(train_iter)
    for iter in process:
        data=(iter[0].to(device),iter[1].to(device),iter[2].to(device))
        label=iter[3].to(device)
        output=model(*data)
        optimizer.zero_grad()
        ls=loss(output.logits,label)

        ls.backward()
        optimizer.step()

        print(f"epoch{epoch+1},loss:{ls.item()}")
        process.update()



  0%|          | 1/476 [00:00<05:10,  1.53it/s]

epoch1,loss:0.7478397488594055


  1%|          | 3/476 [00:00<02:19,  3.38it/s]

epoch1,loss:0.6462320685386658


  1%|          | 5/476 [00:01<01:48,  4.35it/s]

...

epoch25,loss:0.0003909182851202786


506it [02:45,  2.90it/s]

epoch25,loss:0.00016447364760097116


100%|██████████| 476/476 [02:45<00:00,  2.87it/s]

epoch25,loss:0.0009093551780097187


In [ ]:
model.save_pretrained("/content/drive/MyDrive/tweet_disaster_model")

In [12]:
model.from_pretrained("/content/drive/MyDrive/tweet_disaster_model")

BertForSequenceClassification(
  (bert): BertModel(
    (embeddings): BertEmbeddings(
      (word_embeddings): Embedding(30522, 768, padding_idx=0)
      (position_embeddings): Embedding(512, 768)
      (token_type_embeddings): Embedding(2, 768)
      (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (encoder): BertEncoder(
      (layer): ModuleList(
        (0-11): 12 x BertLayer(
          (attention): BertAttention(
            (self): BertSdpaSelfAttention(
              (query): Linear(in_features=768, out_features=768, bias=True)
              (key): Linear(in_features=768, out_features=768, bias=True)
              (value): Linear(in_features=768, out_features=768, bias=True)
              (dropout): Dropout(p=0.1, inplace=False)
            )
            (output): BertSelfOutput(
              (dense): Linear(in_features=768, out_features=768, bias=True)
              (LayerNorm): LayerNorm((768,), eps=1e

In [17]:
model.eval()
df={"id":[], "target":[]}
test_csv=pd.read_csv(test_path)
with torch.no_grad():
  for i, data in enumerate(test_iter):
    data=(data[0].to(device), data[1].to(device), data[2].to(device))
    output=model(*data)
    pred=torch.argmax(output.logits,dim=1).cpu().numpy() #第0维是batchsize
    for idx in range(pred.shape[0]): #batchsize
      id=test_csv["id"][i*Params.batch_size+idx] #i：第i批数据，idx:第i批数据中的第idx个
      df['id'].append(id)
      df['target'].append(pred[idx])
pd.DataFrame(df).to_csv(submission_path,index=False) #index=False表示保存csv文件时，不把索引写进文件中


In [19]:
submission=pd.read_csv(submission_path)
submission[-100:-1]

id  target
3163  10495       0
3164  10497       0
3165  10501       0
3166  10504       0
3167  10507       0
...     ...     ...
3257  10858       0
3258  10861       0
3259  10865       0
3260  10868       0
3261  10874       0

[99 rows x 2 columns]